In [2]:
import pandas as pd
import numpy as np
import os
from tqdm import tqdm
from utils import utils,myplot

from grid_world.data_parser import DataParser
from grid_world.grid_world import GridWorld

import warnings
warnings.filterwarnings('ignore')

df = pd.read_csv(r'wifi_track_data\dacang\track_data\dacang_track_data_final.csv')
df.t = pd.to_datetime(df.t)
mac_list = df.m.unique()

#get path & pos data
df_wifipos = pd.read_csv('wifi_track_data/dacang/pos_data/wifi_pos.csv')
df_path = pd.read_csv('wifi_track_data/dacang/pos_data/path_pos.csv')

%load_ext autoreload
%autoreload 2

## Initialize grid world

In [17]:
env_folder_path = r'wifi_track_data/dacang/grid_data/env_imgs/40_30'
#feature_folder_path = r"wifi_track_data\dacang\grid_data\features_grid\0130_40x30"
expert_traj_path = r"wifi_track_data\dacang\track_data\trajs_sliced_40x30.csv"

world = GridWorld(environments_img_folderPath=env_folder_path,
                  expert_traj_filePath= expert_traj_path,
                  width=40,height=30)

Get experts trajs num:7353
trajs all avg length: 23


parsing environments from folder:: 100%|██████████| 30/30 [00:06<00:00,  4.73it/s]


In [8]:
import torch
import torch.nn as nn
import torch.optim as optim
from tqdm import tqdm
from DMEIRL.value_iteration import value_iteration
import numpy as np
import os
from utils import utils

### Show Dynamics
# Figures 14 (b): Transfer probabilities in upward moving behavior

In [14]:
world.dynamics.shape

(1200, 5, 1200)

In [18]:
world.ShowDynamics(0)

In [19]:
world.ShowDynamics(1)

In [20]:
world.ShowDynamics(2)

In [21]:
world.ShowDynamics(3)

In [22]:
world.ShowDynamics(4)

### Figures 13 (a)(b): Environments and Features

In [23]:
world.ShowEnvironments()

In [24]:
world.features_arr[1]

array([0.11841332, 0.0195579 , 0.00579505, 0.15542857, 0.00611739,
       0.70184095, 0.05332881, 0.65716745, 0.15458279, 0.34942711,
       0.00573833, 0.00297992, 0.00371618, 0.01549289, 0.00311902,
       0.61811096, 0.48895726, 0.00253995, 0.3372086 , 0.29996204,
       0.28344504, 0.01238464, 0.0063025 , 0.65716745, 0.00195777,
       0.15933834, 0.25683345, 0.03648573, 0.0111544 , 0.21936537])

In [25]:
world.features_arr.shape

(206, 30)

In [26]:
world.ShowFeatures()

### Tracks

In [27]:
world.ShowGridWorld_Count()

In [28]:
world.ShowGridWorld_Activated()

In [41]:
df_cluster = pd.read_csv(r'wifi_track_data\dacang\cluster_data\dacang_track_data_resident.csv')
world.experts.ReadCluster(df_cluster)
world.experts.df_trajs_all

m  \
0        7.5-48,74,38,133,29,213+1   
1        7.5-48,74,38,133,29,213+2   
2        7.5-48,74,38,155,214,98+1   
3        7.5-48,74,38,155,214,98+2   
4       7.6-48,74,38,155,214,98+13   
...                            ...   
7348  8.7-124,161,119,201,50,40+22   
7349   8.7-144,173,247,200,14,93+1   
7350   8.7-144,173,247,200,14,93+2   
7351   8.7-176,70,146,156,89,69+12   
7352   8.7-176,70,146,156,89,69+17   

                                                  trajs  cluster  
0     [[420, 1], [460, 0], [460, 3], [459, 0], [459,...       -1  
1     [[877, 3], [876, 0], [876, 3], [875, 3], [874,...       -1  
2     [[420, 1], [460, 0], [460, 3], [459, 0], [459,...       -1  
3     [[877, 0], [877, 0], [877, 0], [877, 0], [877,...       -1  
4     [[788, 4], [789, 0], [789, 1], [829, 4], [830,...       -1  
...                                                 ...      ...  
7348  [[743, 0], [743, 0], [743, 0], [743, 0], [743,...       -1  
7349  [[832, 3], [831, 3], [830, 0], [830, 3], [829,...       -1  
7350  [[374, 0], [374, 0], [374, 0], [374, 0], [374,...       -1  
7351  [[788, 4], [789, 0], [789, 1], [829, 4], [830,...       -1  
7352  [[879, 0], [879, 0], [879, 0], [879, 0], [879,...       -1  

[7353 rows x 3 columns]

In [48]:
world.experts.ApplyCluster([-1])

NameError: name 'bias' is not defined

In [49]:
world.experts.df_trajs

m  \
0        7.5-48,74,38,133,29,213+1   
1        7.5-48,74,38,133,29,213+2   
2        7.5-48,74,38,155,214,98+1   
3        7.5-48,74,38,155,214,98+2   
4       7.6-48,74,38,155,214,98+13   
...                            ...   
7348  8.7-124,161,119,201,50,40+22   
7349   8.7-144,173,247,200,14,93+1   
7350   8.7-144,173,247,200,14,93+2   
7351   8.7-176,70,146,156,89,69+12   
7352   8.7-176,70,146,156,89,69+17   

                                                  trajs  cluster  
0     [[420, 1], [460, 0], [460, 3], [459, 0], [459,...       -1  
1     [[877, 3], [876, 0], [876, 3], [875, 3], [874,...       -1  
2     [[420, 1], [460, 0], [460, 3], [459, 0], [459,...       -1  
3     [[877, 0], [877, 0], [877, 0], [877, 0], [877,...       -1  
4     [[788, 4], [789, 0], [789, 1], [829, 4], [830,...       -1  
...                                                 ...      ...  
7348  [[743, 0], [743, 0], [743, 0], [743, 0], [743,...       -1  
7349  [[832, 3], [831, 3], [830, 0], [830, 3], [829,...       -1  
7350  [[374, 0], [374, 0], [374, 0], [374, 0], [374,...       -1  
7351  [[788, 4], [789, 0], [789, 1], [829, 4], [830,...       -1  
7352  [[879, 0], [879, 0], [879, 0], [879, 0], [879,...       -1  

[7353 rows x 3 columns]

### previous world

In [52]:
#env_folder_path = r'wifi_track_data/dacang/grid_data/env_imgs/40_30'
feature_folder_path = r"wifi_track_data\dacang\grid_data\features_grid\0918_40x30"
expert_traj_path = r"wifi_track_data\dacang\track_data\trajs_sliced_40x30.csv"

world_pre = GridWorld(features_folderPath=feature_folder_path,
                  expert_traj_filePath= expert_traj_path,
                  width=40,height=30)

Get experts trajs num:7353
trajs all avg length: 23


In [53]:
world_pre.features_arr.shape

(206, 30)

In [54]:
world_pre.ShowFeatures()